In [ ]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer, TextClassificationPipeline
import torch
import gradio as gr

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
# Load the fine-tuned model and tokenizer
new_model = AutoModelForSequenceClassification.from_pretrained('roberta-rating')
new_tokenizer = AutoTokenizer.from_pretrained('roberta-rating')


# Create a classification pipeline
classifier = TextClassificationPipeline(model=new_model, tokenizer=new_tokenizer, device=device)

# Add label mapping for sentiment analysis (assuming LABEL_0 = 'negative' and LABEL_1 = 'positive')
label_mapping = {1: '1/5', 2: '2/5', 3: '3/5', 4: '4/5', 5: '5/5'}

def evaluate(text):
    result = classifier(text)
    return label_mapping[int(result[0]['label'].split('_')[1])] + ".", result[0]['score']

iface = gr.Interface(
    fn=evaluate,
    inputs=gr.Textbox(label="Review"),
    outputs=[gr.Textbox(label="Evaluation"), gr.Textbox(label="Score")],
    title='Write a review',
    description="Write a product review, and the model will evaluate its numerical rating"
)

iface.launch(share=True)